Install Packages

In [ ]:
!pip install tpot mljar-supervised

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 87 kB 2.2 MB/s 
     |████████████████████████████████| 112 kB 42.4 MB/s 
     |████████████████████████████████| 193.6 MB 53 kB/s 
     |████████████████████████████████| 139 kB 50.4 MB/s 
     |████████████████████████████████| 2.0 MB 67.6 MB/s 
     |████████████████████████████████| 76.6 MB 1.2 MB/s 
     |████████████████████████████████| 72 kB 541 kB/s 
     |████████████████████████████████| 575 kB 53.4 MB/s 
     |████████████████████████████████| 72 kB 352 kB/s 
     |████████████████████████████████| 348 kB 56.1 MB/s 
     |████████████████████████████████| 209 kB 71.1 MB/s 
     |████████████████████████████████| 81 kB 6.8 MB/s 
     |████████████████████████████████| 78 kB 4.9 MB/s 
     |████████████████████████████████| 50 kB 6.4 MB/s 
     |████████████████████████████████| 147 kB 54.7 MB/s 
     |████████████████████████████████| 112

In [ ]:
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split
from supervised.automl import AutoML

In [ ]:
import pandas as pd

In [ ]:
sparcs = pd.read_csv('https://raw.githubusercontent.com/hantswilliams/HHA-507-2022/main/autoML/datasets/data_sparcs.csv')
sparcs

Health Service Area Hospital County  Operating Certificate Number  \
0              Western NY        Allegany                      226700.0   
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23578         Long Island         Suffolk                     5157003.0   
23579         Long Island         Suffolk                     5157003.0   
23580         Long Island         Suffolk                     5157003.0   
23581         Long Island         Suffolk                     5157003.0   
23582         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
0             37.0                         Cuba Memorial Hospital Inc   
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23578        943.0                     St Catherine of Siena Hospital   
23579        943.0                     St Catherine of Siena Hospital   
23580        943.0                     St Catherine of Siena Hospital   
23581        943.0                     St Catherine of Siena Hospital   
23582        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
0         30 to 49                 147      M       White  Not Span/Hispanic   
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23578  70 or Older                 117      F       White  Not Span/Hispanic   
23579      0 to 17                 117      F  Other Race   Spanish/Hispanic   
23580     30 to 49                 117      M       White  Not Span/Hispanic   
23581  70 or Older                 117      M       White  Not Span/Hispanic   
23582  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Risk of Mortality APR Medical Surgical Description  \
0      ...                 Minor                          Medical   
1      ...                 Minor                          Medical   
2      ...                 Minor                          Medical   
3      ...              Moderate                          Medical   
4      ...                 Major                          Medical   
...    ...                   ...                              ...   
23578  ...              Moderate                          Medical   
23579  ...                 Minor                          Medical   
23580  ...                 Minor                          Medical   
23581  ...                 Major                          Medical   
23582  ...                 Major                          Medical   

             Payment Typology 1        Payment Typology 2  Payment Typology 3  \
0      Private Health Insurance                       NaN                 NaN   
1        Blue Cross/Blue Shield                  Self-Pay            Self-Pay   
2                      Self-Pay                  Self-Pay            Self-Pay   
3                      Medicare                  Medicare            Self-Pay   
4        Blue Cross/Blue Shield  

In [ ]:
sparcs.columns

Index(['Health Service Area', 'Hospital County',
       'Operating Certificate Number', 'Facility Id', 'Facility Name',
       'Age Group', 'Zip Code - 3 digits', 'Gender', 'Race', 'Ethnicity',
       'Length of Stay', 'Type of Admission', 'Patient Disposition',
       'Discharge Year', 'CCS Diagnosis Code', 'CCS Diagnosis Description',
       'CCS Procedure Code', 'CCS Procedure Description', 'APR DRG Code',
       'APR DRG Description', 'APR MDC Code', 'APR MDC Description',
       'APR Severity of Illness Code', 'APR Severity of Illness Description',
       'APR Risk of Mortality', 'APR Medical Surgical Description',
       'Payment Typology 1', 'Payment Typology 2', 'Payment Typology 3',
       'Birth Weight', 'Abortion Edit Indicator',
       'Emergency Department Indicator', 'Total Charges', 'Total Costs'],
      dtype='object')

In [ ]:
sparcs['Type of Admission'].describe()

count         23583
unique            6
top       Emergency
freq          14968
Name: Type of Admission, dtype: object

In [ ]:
sparcs['Type of Admission'].value_counts()

Emergency        14968
Elective          4508
Newborn           2285
Urgent            1743
Trauma              63
Not Available       16
Name: Type of Admission, dtype: int64

In [ ]:
sparcs['Gender'].value_counts()

F    13187
M    10395
U        1
Name: Gender, dtype: int64

In [ ]:
sparcs['Total Charges'].describe()

count    2.358300e+04
mean     4.344052e+04
std      8.434949e+04
min      1.000000e+00
25%      1.226175e+04
50%      2.375403e+04
75%      4.702837e+04
max      4.410671e+06
Name: Total Charges, dtype: float64

Multiclass

In [114]:
x = sparcs.drop(columns=['Type of Admission'])

In [115]:
y = sparcs["Type of Admission"]

In [116]:
x

Health Service Area Hospital County  Operating Certificate Number  \
0              Western NY        Allegany                      226700.0   
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23578         Long Island         Suffolk                     5157003.0   
23579         Long Island         Suffolk                     5157003.0   
23580         Long Island         Suffolk                     5157003.0   
23581         Long Island         Suffolk                     5157003.0   
23582         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
0             37.0                         Cuba Memorial Hospital Inc   
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23578        943.0                     St Catherine of Siena Hospital   
23579        943.0                     St Catherine of Siena Hospital   
23580        943.0                     St Catherine of Siena Hospital   
23581        943.0                     St Catherine of Siena Hospital   
23582        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
0         30 to 49                 147      M       White  Not Span/Hispanic   
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23578  70 or Older                 117      F       White  Not Span/Hispanic   
23579      0 to 17                 117      F  Other Race   Spanish/Hispanic   
23580     30 to 49                 117      M       White  Not Span/Hispanic   
23581  70 or Older                 117      M       White  Not Span/Hispanic   
23582  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Medical Surgical Description        Payment Typology 1  \
0      ...                          Medical  Private Health Insurance   
1      ...                          Medical    Blue Cross/Blue Shield   
2      ...                          Medical                  Self-Pay   
3      ...                          Medical                  Medicare   
4      ...                          Medical    Blue Cross/Blue Shield   
...    ...                              ...                       ...   
23578  ...                          Medical                  Medicare   
23579  ...                          Medical  Private Health Insurance   
23580  ...                          Medical                  Medicaid   
23581  ...                          Medical                  Medicare   
23582  ...                          Medical                  Medicare   

             Payment Typology 2  Payment Typology 3 Birth Weight  \
0                           NaN                 NaN            0   
1                      Self-Pay            Self-Pay            0   
2                      Self-Pay            Self-Pay         2900   
3                      Medicare            Self-Pay            0   
4                      Medicare            Self-Pa

In [117]:
y

0           Urgent
1           Urgent
2          Newborn
3        Emergency
4        Emergency
           ...    
23578    Emergency
23579      Newborn
23580       Urgent
23581    Emergency
23582    Emergency
Name: Type of Admission, Length: 23583, dtype: object

In [118]:
x_train, x_test, y_train, y_test = train_test_split(x, y, stratify=y, test_size= 0.25)

In [119]:
x_test

Health Service Area Hospital County  Operating Certificate Number  \
12703       New York City           Kings                     7001021.0   
18562       New York City          Queens                     7003004.0   
20471         Long Island         Suffolk                     5151001.0   
2631         Finger Lakes          Monroe                     2701005.0   
2245         Finger Lakes          Monroe                     2701003.0   
...                   ...             ...                           ...   
9911        New York City           Bronx                     7000006.0   
16505       New York City       Manhattan                     7002053.0   
16039       New York City       Manhattan                     7002054.0   
20324         Long Island         Suffolk                     5151001.0   
20358         Long Island         Suffolk                     5151001.0   

       Facility Id                                      Facility Name  \
12703       1306.0                        New York Methodist Hospital   
18562       1630.0                  Long Island Jewish Medical Center   
20471        245.0                                University Hospital   
2631         413.0                           Strong Memorial Hospital   
2245         411.0                         Rochester General Hospital   
...            ...                                                ...   
9911        1169.0  Montefiore Medical Center - Henry & Lucy Moses...   
16505       1463.0                               NYU Hospitals Center   
16039       1458.0  New York Presbyterian Hospital - New York Weil...   
20324        245.0                                University Hospital   
20358        245.0                                University Hospital   

         Age Group Zip Code - 3 digits Gender                    Race  \
12703     50 to 69                 112      M              Other Race   
18562     50 to 69                 117      F                   White   
20471  70 or Older                 117      F                   White   
2631      50 to 69                 136      F                   White   
2245      18 to 29                 146      F  Black/African American   
...            ...                 ...    ...                     ...   
9911      30 to 49                 104      F              Other Race   
16505      0 to 17                 100      F                   White   
16039  70 or Older                 111      M                   White   
20324     18 to 29                 119      F  Black/African American   
20358     18 to 29                 117      M                   White   

               Ethnicity  ... APR Medical Surgical Description  \
12703  Not Span/Hispanic  ...                         Surgical   
18562  Not Span/Hispanic  ...                         Surgical   
20471  Not Span/Hispanic  ...                          Medical   
2631   Not Span/Hispanic  ...                          Medical   
2245   Not Span/Hispanic  ...                          Medical   
...                  ...  ...                              ...   
9911   Not Span/Hispanic  ...                         Surgical   
16505  Not Span/Hispanic  ...                          Medical   
16039  Not Span/Hispanic  ...                         Surgical   
20324  Not Span/Hispanic  ...                          Medical   
20358  Not Span/Hispanic  ...                          Medical   

             Payment Typology 1      Payment Typology 2  \
12703  Private Health Insurance                     NaN   
18562  Private Health Insurance                Self-Pay   
20471                  Medicare  Blue Cross/Blue Shield   
2631     Blue Cross/Blue Shield                Self-Pay   
2245                   Medicaid                     NaN   
...                         ...                     ...   
9911                   Medicare                Medicare   
16505  Private Health Insurance                     NaN   
16039                  Medi

In [120]:
automl = AutoML(results_path="Sparcs_Admission", mode="Explain")

In [121]:
automl.fit(x_train, y_train)

Linear algorithm was disabled.
This model has already been fitted. You can use predict methods or select a new 'results_path' for a new 'fit()'.


In [122]:
pred = automl.predict(x_test)
pred

array(['Emergency', 'Elective', 'Emergency', ..., 'Elective', 'Emergency',
       'Emergency'], dtype=object)

In [123]:
automl.report()

Regression

In [131]:
x_cols = [c for c in sparcs.columns if c != 'Total Charges']
X = sparcs[x_cols]
Y = sparcs['Total Charges']

In [132]:
X

Health Service Area Hospital County  Operating Certificate Number  \
0              Western NY        Allegany                      226700.0   
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23578         Long Island         Suffolk                     5157003.0   
23579         Long Island         Suffolk                     5157003.0   
23580         Long Island         Suffolk                     5157003.0   
23581         Long Island         Suffolk                     5157003.0   
23582         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
0             37.0                         Cuba Memorial Hospital Inc   
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23578        943.0                     St Catherine of Siena Hospital   
23579        943.0                     St Catherine of Siena Hospital   
23580        943.0                     St Catherine of Siena Hospital   
23581        943.0                     St Catherine of Siena Hospital   
23582        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
0         30 to 49                 147      M       White  Not Span/Hispanic   
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23578  70 or Older                 117      F       White  Not Span/Hispanic   
23579      0 to 17                 117      F  Other Race   Spanish/Hispanic   
23580     30 to 49                 117      M       White  Not Span/Hispanic   
23581  70 or Older                 117      M       White  Not Span/Hispanic   
23582  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Risk of Mortality APR Medical Surgical Description  \
0      ...                 Minor                          Medical   
1      ...                 Minor                          Medical   
2      ...                 Minor                          Medical   
3      ...              Moderate                          Medical   
4      ...                 Major                          Medical   
...    ...                   ...                              ...   
23578  ...              Moderate                          Medical   
23579  ...                 Minor                          Medical   
23580  ...                 Minor                          Medical   
23581  ...                 Major                          Medical   
23582  ...                 Major                          Medical   

             Payment Typology 1        Payment Typology 2  Payment Typology 3  \
0      Private Health Insurance                       NaN                 NaN   
1        Blue Cross/Blue Shield                  Self-Pay            Self-Pay   
2                      Self-Pay                  Self-Pay            Self-Pay   
3                      Medicare                  Medicare            Self-Pay   
4        Blue Cross/Blue Shield  

In [133]:
Y

0         4757.01
1         5090.25
2         4948.50
3         4719.75
4        50384.75
           ...   
23578    50833.00
23579    10948.00
23580    46421.00
23581    46122.00
23582    32225.00
Name: Total Charges, Length: 23583, dtype: float64

In [134]:
automl_reg = AutoML(results_path="Sparcs_totalcharges", mode="Explain")

In [143]:
automl_reg.fit(X, Y)

This model has already been fitted. You can use predict methods or select a new 'results_path' for a new a 'fit()'.


In [137]:
sparcs["predictions"] = automl_reg.predict(X)

In [138]:
print("Predictions")
print(sparcs[['Total Charges', 'predictions']].head())

Predictions
   Total Charges   predictions
0        4757.01   4762.187988
1        5090.25   5097.455078
2        4948.50   4948.528809
3        4719.75   4723.353027
4       50384.75  42594.515625


In [139]:
automl_reg.report()

Download outputs

In [144]:
# get current working directory
import os
os.getcwd()

'/content'

In [147]:
folders = os.listdir()
foldersML = [x for x in folders if x.startswith('Sparcs')]
print(foldersML)

['Sparcs_Admission', 'Sparcs_totalcharges']


In [151]:
!zip -r /content/sparcs_type_of_admission.zip /content/Sparcs_Admission

  adding: content/Sparcs_Admission/ (stored 0%)
  adding: content/Sparcs_Admission/params.json (deflated 61%)
  adding: content/Sparcs_Admission/5_Default_RandomForest/ (stored 0%)
  adding: content/Sparcs_Admission/5_Default_RandomForest/framework.json (deflated 80%)
  adding: content/Sparcs_Admission/5_Default_RandomForest/learner_fold_0_shap_dependence_class_Newborn.png (deflated 7%)
  adding: content/Sparcs_Admission/5_Default_RandomForest/learner_fold_0_training.log (deflated 55%)
  adding: content/Sparcs_Admission/5_Default_RandomForest/learning_curves.png (deflated 10%)
  adding: content/Sparcs_Admission/5_Default_RandomForest/learner_fold_0_shap_importance.csv (deflated 45%)
  adding: content/Sparcs_Admission/5_Default_RandomForest/shap_importance.png (deflated 15%)
  adding: content/Sparcs_Admission/5_Default_RandomForest/learner_fold_0_importance.csv (deflated 45%)
  adding: content/Sparcs_Admission/5_Default_RandomForest/README.md (deflated 78%)
  adding: content/Sparcs_Admi

In [152]:
!zip -r /content/sparcs_type_of_admission.zip /content/Sparcs_totalcharges

  adding: content/Sparcs_totalcharges/ (stored 0%)
  adding: content/Sparcs_totalcharges/5_Default_Xgboost/ (stored 0%)
  adding: content/Sparcs_totalcharges/params.json (deflated 61%)
  adding: content/Sparcs_totalcharges/5_Default_RandomForest/ (stored 0%)
  adding: content/Sparcs_totalcharges/5_Default_RandomForest/framework.json (deflated 80%)
  adding: content/Sparcs_totalcharges/5_Default_RandomForest/learner_fold_0_training.log (deflated 55%)
  adding: content/Sparcs_totalcharges/5_Default_RandomForest/learning_curves.png (deflated 8%)
  adding: content/Sparcs_totalcharges/5_Default_RandomForest/learner_fold_0_shap_importance.csv (deflated 48%)
  adding: content/Sparcs_totalcharges/5_Default_RandomForest/learner_fold_0_shap_dependence.png (deflated 5%)
  adding: content/Sparcs_totalcharges/5_Default_RandomForest/shap_importance.png (deflated 15%)
  adding: content/Sparcs_totalcharges/5_Default_RandomForest/learner_fold_0_importance.csv (deflated 58%)
  adding: content/Sparcs_tot